In [2]:
!pip install pydiarization        
!pip install pyannote.audio

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.8/56.8 kB 840.2 kB/s eta 0:00:00a 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 117.0/117.0 kB 1.8 MB/s eta 0:00:00a 0:00:01
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.6/59.6 kB 2.7 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 208.7/208.7 kB 4.2 MB/s eta 0:00:0000:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.6/44.6 kB 2.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 20.8 MB/s eta 0:00:00a 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 79.5/79.5 kB 3.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.5/58.5 kB 3.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.1/48.1 kB 2.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 51.4/51.4 kB 2.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 118.6/118.6 kB 5.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━

In [22]:
import pydub                      # converting sample rate

import os                         # file & directory handling
import random                     # random seeding
import IPython                    # displaying audio

from tqdm.notebook import tqdm    # progress bar

import numpy as np                # array handling
import scipy.io                   # scientific data handling

import matplotlib.pyplot as plt   # visualization framework
import seaborn as sns             # additional visualization support

import tensorflow as tf           # deep learning
from tensorflow import keras      # deep learning

from scipy.io import wavfile
from pydiarization.diarization_wrapper import rttm_to_string

from IPython.core.display import display

import sklearn
from pyannote.audio import Pipeline

from sklearn import preprocessing
from sklearn import cluster
from pydub import AudioSegment as am
import librosa
from glob import glob

from transformers import (
    AutoTokenizer, AutoFeatureExtractor, AutoModelForCTC, 
    AutoProcessor, Wav2Vec2Model, HubertForCTC, 
    HubertModel, Data2VecAudioForCTC, Data2VecAudioModel,
    AutoModelForAudioXVector, Wav2Vec2Processor, Wav2Vec2ForCTC, Wav2Vec2FeatureExtractor, Wav2Vec2CTCTokenizer
)

import torch

# Getting familiar with the dataset

references:
https://www.kaggle.com/code/washingtongold/identifying-speaker-change

In [4]:
SAMPLE_INDEX = 0

path = '../input/voxconverse-dataset/voxconverse_dev_wav/audio'
file = os.listdir(path)[SAMPLE_INDEX]
samplerate, data = wavfile.read(os.path.join(path, file))

print(f'FILENAME: {file}')
print(f'LENGTH:   {round(len(data)/samplerate, 2)} seconds')
print()

scipy.io.wavfile.write('temp.wav', samplerate, data)
display(IPython.display.Audio('temp.wav'))

FILENAME: azisu.wav
LENGTH:   194.14 seconds



In [5]:
path = '../input/voxconverse-dataset/labels/dev'
file = file.split('.')[0] + '.rttm'

print(rttm_to_string(os.path.join(path, file)))

SPEAKER azisu 1 7.960000 5.720000 <NA> <NA> spk00 <NA> <NA>
SPEAKER azisu 1 138.600000 13.840000 <NA> <NA> spk00 <NA> <NA>
SPEAKER azisu 1 156.880000 6.480000 <NA> <NA> spk00 <NA> <NA>
SPEAKER azisu 1 169.840000 4.920000 <NA> <NA> spk00 <NA> <NA>
SPEAKER azisu 1 180.160000 1.960000 <NA> <NA> spk00 <NA> <NA>
SPEAKER azisu 1 95.440000 1.000000 <NA> <NA> spk01 <NA> <NA>
SPEAKER azisu 1 102.000000 36.600000 <NA> <NA> spk01 <NA> <NA>
SPEAKER azisu 1 150.760000 7.360000 <NA> <NA> spk01 <NA> <NA>
SPEAKER azisu 1 159.160000 12.560000 <NA> <NA> spk01 <NA> <NA>
SPEAKER azisu 1 172.480000 2.800000 <NA> <NA> spk01 <NA> <NA>
SPEAKER azisu 1 51.200000 2.240000 <NA> <NA> spk02 <NA> <NA>
SPEAKER azisu 1 36.960000 7.360000 <NA> <NA> spk00 <NA> <NA>
SPEAKER azisu 1 101.760000 1.200000 <NA> <NA> spk02 <NA> <NA>
SPEAKER azisu 1 190.840000 1.640000 <NA> <NA> spk02 <NA> <NA>
SPEAKER azisu 1 0.520000 8.120000 <NA> <NA> spk03 <NA> <NA>
SPEAKER azisu 1 9.440000 1.320000 <NA> <NA> spk03 <NA> <NA>
SPEAKER azisu 

In [6]:
def readRTTM(file):
    data = {}
    rttm = rttm_to_string(file)
    rttm = rttm.split('\n')[:-1]
    for line in rttm:
        data[float(line.split(' ')[3])] = [float(line.split(' ')[4]),
                                           line.split(' ')[7]]
    starts, intervals, speakers = [], [], []
    for start in sorted(data): # sort returns by start
        starts.append(start)
        intervals.append(data[start][0])
        speakers.append(data[start][1])
    return starts, intervals, speakers

In [7]:
readRTTM(os.path.join(path, file))

([0.52,
  7.96,
  9.44,
  12.8,
  36.96,
  43.56,
  45.56,
  51.2,
  53.88,
  57.48,
  74.16,
  88.0,
  95.44,
  101.76,
  102.0,
  109.88,
  123.96,
  125.2,
  138.6,
  150.76,
  156.88,
  159.16,
  169.84,
  172.48,
  174.48,
  177.88,
  180.16,
  190.84],
 [8.12,
  5.72,
  1.32,
  24.2,
  7.36,
  13.72,
  1.6,
  2.24,
  1.08,
  30.36,
  0.52,
  14.28,
  1.0,
  1.2,
  36.6,
  2.12,
  0.88,
  0.44,
  13.84,
  7.36,
  6.48,
  12.56,
  4.92,
  2.8,
  3.24,
  16.24,
  1.96,
  1.64],
 ['spk03',
  'spk00',
  'spk03',
  'spk03',
  'spk00',
  'spk03',
  'spk00',
  'spk02',
  'spk00',
  'spk00',
  'spk03',
  'spk00',
  'spk01',
  'spk02',
  'spk01',
  'spk00',
  'spk00',
  'spk00',
  'spk00',
  'spk01',
  'spk00',
  'spk01',
  'spk00',
  'spk01',
  'spk03',
  'spk03',
  'spk00',
  'spk02'])

# Preparing data and extracting embeddings

In [24]:
train_wave_pathes = glob(
    "/kaggle/input/voxconverse-dataset/voxconverse_dev_wav/audio/*.wav", recursive=True
)
test_wave_pathes = glob(
    "/kaggle/input/voxconverse-dataset/voxconverse_dev_wav/audio/*.wav", recursive=True
)
train_wave_pathes.sort()
test_wave_pathes.sort()

train_wave_pathes[:10]

['/kaggle/input/voxconverse-dataset/voxconverse_dev_wav/audio/abjxc.wav',
 '/kaggle/input/voxconverse-dataset/voxconverse_dev_wav/audio/afjiv.wav',
 '/kaggle/input/voxconverse-dataset/voxconverse_dev_wav/audio/ahnss.wav',
 '/kaggle/input/voxconverse-dataset/voxconverse_dev_wav/audio/aisvi.wav',
 '/kaggle/input/voxconverse-dataset/voxconverse_dev_wav/audio/akthc.wav',
 '/kaggle/input/voxconverse-dataset/voxconverse_dev_wav/audio/ampme.wav',
 '/kaggle/input/voxconverse-dataset/voxconverse_dev_wav/audio/asxwr.wav',
 '/kaggle/input/voxconverse-dataset/voxconverse_dev_wav/audio/atgpi.wav',
 '/kaggle/input/voxconverse-dataset/voxconverse_dev_wav/audio/aufkn.wav',
 '/kaggle/input/voxconverse-dataset/voxconverse_dev_wav/audio/azisu.wav']

In [26]:
print(len(train_wave_pathes),len(test_wave_pathes))

216 216


In [17]:
class XVectorExtractor:
    def __init__(
        self,
        model_name,
        device="cpu",
        do_normalize=True
    ):
        self.feature_extractor = AutoFeatureExtractor.from_pretrained(model_name)
        self.model = AutoModelForAudioXVector.from_pretrained(model_name).to(device)
        self.do_normalize = do_normalize

    def extract_features(
        self,
        wave_pathes,
        sample_rate
    ):
        features = []
        for wave_path in tqdm(wave_pathes):
            wave, _ = librosa.load(wave_path, sr=sample_rate)
            inputs = self.feature_extractor([wave], sampling_rate=sample_rate, return_tensors="pt").input_values
            with torch.no_grad():
                embeddings = self.model(inputs.cuda()).embeddings
            if self.do_normalize:
                embeddings = torch.nn.functional.normalize(embeddings, dim=-1)
            embeddings = embeddings.cpu()
            features.append(embeddings)
        return torch.cat(features, dim=0)

In [35]:
w2v2_xvector_model = XVectorExtractor(
    model_name="anton-l/wav2vec2-base-superb-sv",
    device="cuda",
    do_normalize=True
)

Some weights of the model checkpoint at anton-l/wav2vec2-base-superb-sv were not used when initializing Wav2Vec2ForXVector: ['wav2vec2.encoder.pos_conv_embed.conv.weight_g', 'wav2vec2.encoder.pos_conv_embed.conv.weight_v']
- This IS expected if you are initializing Wav2Vec2ForXVector from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing Wav2Vec2ForXVector from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of Wav2Vec2ForXVector were not initialized from the model checkpoint at anton-l/wav2vec2-base-superb-sv and are newly initialized: ['wav2vec2.encoder.pos_conv_embed.conv.parametrizations.weight.original0', 'wav2vec2.encoder.pos_conv_embed.conv.parametrizations.weight.original1']
You should pr

In [36]:
w2v2_xvector_model.extract_features([train_wave_pathes[0]], sample_rate=16_000)

  0%|          | 0/1 [00:00<?, ?it/s]

tensor([[-1.3470e-02, -1.9526e-02, -2.2595e-02, -1.1120e-03,  5.3127e-03,
         -6.1308e-02, -2.2547e-02,  2.1546e-02, -4.9274e-02, -2.0312e-02,
         -1.0941e-01, -7.1550e-02, -1.9818e-02, -3.9962e-02, -4.9219e-02,
         -5.9925e-03, -2.2333e-02, -2.1991e-02, -2.9450e-02, -1.9972e-02,
         -1.5530e-01, -1.5670e-02,  2.8784e-02, -6.0576e-02, -1.1809e-01,
         -2.9614e-02, -2.9036e-02, -2.4280e-02, -1.9172e-02, -1.3901e-02,
         -1.6972e-02, -2.5183e-02, -9.3310e-02, -1.7991e-02, -2.3371e-02,
         -2.2019e-02, -9.4757e-02, -4.3108e-02, -2.0765e-02, -2.1153e-02,
         -9.7772e-02, -2.0470e-02, -2.5300e-02, -2.4307e-02, -7.5320e-02,
         -3.2572e-02, -2.0699e-02, -2.0737e-02, -2.5593e-02,  2.2970e-03,
         -1.6451e-02, -1.7389e-02,  5.0422e-03, -1.0650e-01, -1.0139e-01,
         -5.0994e-02, -1.9238e-02, -2.4095e-01, -3.4275e-02, -1.8234e-02,
         -2.2439e-02, -1.6958e-01, -1.8870e-02, -5.4195e-02, -3.4437e-02,
         -3.8632e-02,  2.5350e-03, -1.

In [37]:
train_w2v2_embs = w2v2_xvector_model.extract_features(
    train_wave_pathes[:2], 
    sample_rate=16_000
)
test_w2v2_embs = w2v2_xvector_model.extract_features(
    test_wave_pathes[:2], 
    sample_rate=16_000
)

  0%|          | 0/2 [00:00<?, ?it/s]

  0%|          | 0/2 [00:00<?, ?it/s]

In [38]:
train_w2v2_embs

tensor([[-0.0135, -0.0195, -0.0226,  ..., -0.0144, -0.0216, -0.0183],
        [-0.0172, -0.0276, -0.0246,  ..., -0.0161, -0.0259, -0.0245]])